# Robust Regression

## Imports

In [ ]:
# <include-robust_regression/utils.py>

In [ ]:
# <imports>
import numpy as np
import pandas as pd
import plotly.io as pio

from robust_regression import utils

pd.options.plotting.backend = "plotly"
pio.templates.default = "seaborn"

## Summary

This assignment compares the performance characteristics of three linear different linear models, an ordinarily least squares model and two robust linear model, one with a with Huber T penalty function and the other with a Tukey Biweight penalty function. We use a simple bivariate input comprised of the geometric average of the weekly "return" on 5-year CDS rates for a selection of 11 other public traded companies and the weekly return on adjusted closing price to predict weekly 5-year CDS return. In order to have a reasonable number of instances of each model type to analyze, we fit models for successive periods of 16 weeks beginning 2018-01-02 and ending 2020-12-16 (155 periods). We then analyze the residuals from predictions of the immediately following four weeks for each period.

### Analyses:
* Comparison of histograms of residuals and scaled residuals
* Comparison of summary statistics of residuals and scaled residuals
* Cumulative mean error by error quantile, scaled and unscaled
* Relative cumulative mean error by quantile
* Residual-residual plots

In [ ]:
date_range = pd.date_range("2018-01-03", "2021-04-30", freq="7D")
df_data = utils.get_data(date_range)
df_data.head()

series              adj_close  r_equity  r_spread  spread5y   r_index
date       ticker                                                    
2018-01-10 BA      305.145884  0.072711 -0.059278  0.001585  0.005486
           C        68.482990  0.014111 -0.002452  0.004070  0.000320
           DD       99.438127  0.015620  0.012211  0.002455 -0.001013
           F        11.202605  0.020939  0.017057  0.008620 -0.001454
           GE       17.577243  0.042025  0.009481  0.004115 -0.000765

In [ ]:
df_data.describe()

series    adj_close     r_equity     r_spread     spread5y      r_index
count   2076.000000  2076.000000  2076.000000  2076.000000  2076.000000
mean      80.308101     0.000234     0.003946     0.008423     0.003946
std       77.685027     0.057467     0.107430     0.009822     0.080174
min        4.400000    -0.618276    -0.483083     0.001400    -0.270859
25%       29.939171    -0.021863    -0.041787     0.003876    -0.035819
50%       60.526341     0.000999    -0.000733     0.005189    -0.003761
75%      101.073961     0.025534     0.035766     0.008344     0.031629
max      425.288761     0.443311     1.337747     0.133911     0.647429

## Analysis

We start off comparing the three different models, all without forcing the intercept through zero. The chart below compares histograms of the errors on returns unit basis as well as on scaled basis. We can see that on a scaled basis that the robust linear models have a much narrower range. It is also worth noting the extreme nature of the outliers on a scaled basis. This is likely due to the fact that both the in-sample and out of sample periods contain relatively few observations and as such are subject to dramatics swings. From the summary statistics above, we can see that we had a maximum weekly change of over 130%, but a median of only -0.07%.

In [ ]:
models = [
    {"model": "OLS", "penalty": None, "B0": 1, "name": "OLS"},
    {"model": "RLM", "penalty": "Huber", "B0": 1, "name": "RLM:Huber"},
    {"model": "RLM", "penalty": "Tukey", "B0": 1, "name": "RLM:Tukey"},
]

In [ ]:
dfs_error = {model["name"]: utils.get_errors(df_data, **model)[0] for model in models}

We start off with a

In [ ]:
utils.make_histograms(dfs_error)

### All Data

Here we examine summary statistics of the scaled and unscaled residuals as well as the scale parameter from the regression models for the entire set of observations, all on an absolute value basis. The statistics on an unscaled basis are all relatively similar, although as expected both the mean and median unscaled error the RLM models are lower than they are for the OLS model. On a scaled basis, the difference is much more dramatic. This is obviously as a result of the scale parameter being an order of magnitude less. I'm not sure why the scale would be so much less. In fact, I would have thought that since the RLM models put less weight on the outliers that they would have had lower scale parameters.

In [ ]:
stats_list = []
for name, df_e in dfs_error.items():
    stats = df_e[["resid", "sresid", "scale"]].abs().describe().loc[["mean", "50%", "std"]]
    stats["model"] = name
    stats.index.name = "stat"
    stats_list.append(stats)

In [ ]:
pd.concat(stats_list).reset_index().set_index(["model", "stat"]).unstack("stat")

resid                        sresid                        \
stat            50%      mean       std       50%       mean        std   
model                                                                     
OLS        0.029632  0.047861  0.065214  8.158049  15.165991  25.684095   
RLM:Huber  0.029006  0.047041  0.063701  0.672486   1.085399   1.513268   
RLM:Tukey  0.029142  0.047321  0.064318  0.672877   1.092791   1.525533   

              scale                      
stat            50%      mean       std  
model                                    
OLS        0.003316  0.005951  0.007763  
RLM:Huber  0.039790  0.047717  0.024007  
RLM:Tukey  0.039973  0.047485  0.023826

### By Quantiles

To analyze the performance of the models excluding outliers, we examine the cumulative mean residual by quantile. What we would expect to see is that the cumulative mean error is lower for the RLM models through the lower quantiles and gets closer to the OLS mean error only as all of the errors, including the outliers in the upper quantiles, are included. In this first chart it is a little hard to distinquish differences between the models, but the general shape of the curve obviously makes sense - the cumulative mean error increase as higher quantile errors are included.

In [ ]:
utils.make_cum_error_chart(dfs_error, scaled=False)

On a scaled basis, we see that the RLM models not only have lower errors, as we saw above in the aggregate statistics, but also the slope of the increase as higher quantile errors are included is much smaller.

In [ ]:
utils.make_cum_error_chart(dfs_error, scaled=True)

To gain a better understanding of the relative differences, we can plot something of an efficiency statistic through the quantiles where we divide one of the curves by another. Below is the chart of RLM:Huber against the OLS model. This shows that relative errors at the lower quantiles are actually higher for the RLM model and then the average comes down as the higher quantiles are included. It is also easier to see tht overall there was an approximate two point difference in the average errors between the two models.


In [ ]:
utils.make_efficiency_chart({models[1]["name"]: dfs_error[models[1]["name"]], models[0]["name"]: dfs_error[models[0]["name"]]})

The relative differences between each of the RLM models and the OLS model are similar. Let's compare the two RLM models. This is the Huber over the Tukey. Given the way the penalty functions work, with the Huber treating linearly anything over the default value for the z-score of 1.34 and Tukey not increasing weight at all for anything over about five scale units, we would expect the residuals for the Huber to be smaller for the outliers (since it effectively includes more of them in determining its parameters), and that is what we see, albeit at nearly de minimus level. Similar logic explains the relatively worse performance of the Huber model for th lower quantile errors. This could be used to support the conclusion that the Huber model is preferable to the Tukey one in that trading off worse relative performance on the smallest errors for better performance on the worse ones seems advantageous.

In [ ]:
utils.make_efficiency_chart({
    models[1]["name"]: dfs_error[models[1]["name"]],
    models[2]["name"]: dfs_error[models[2]["name"]]
})

On a scaled basis, the Huber model appears to be marginally better throughout more of hte error range, although likely not to a statistically significant extent.

In [ ]:
utils.make_efficiency_chart({
    models[1]["name"]: dfs_error[models[1]["name"]],
    models[2]["name"]: dfs_error[models[2]["name"]],
},scaled=True)

### Residual-Residual Plots

In [ ]:
utils.make_residual_chart({
    models[0]["name"]: dfs_error[models[0]["name"]],
    models[1]["name"]: dfs_error[models[1]["name"]],
},scaled=False)

In [ ]:
utils.make_residual_chart({
    models[1]["name"]: dfs_error[models[1]["name"]],
    models[2]["name"]: dfs_error[models[2]["name"]],
},scaled=True)

## Single Regressions

### OLS

In [ ]:
df_in = df_data.loc[list(date_range[1:85])]
df_out = df_data.loc[list(date_range[85:])]
B0 = 1

In [ ]:
y_in, X_in = utils.dmatrices(
    f"r_spread ~ r_index + r_equity + {B0}", data=df_in, return_type="dataframe"
)

In [ ]:
res = utils.sm.OLS(y_in, X_in).fit()

In [ ]:
print(res.summary())

                            OLS Regression Results                            
Dep. Variable:               r_spread   R-squared:                       0.455
Model:                            OLS   Adj. R-squared:                  0.454
Method:                 Least Squares   F-statistic:                     419.6
Date:                Sun, 16 May 2021   Prob (F-statistic):          3.29e-133
Time:                        09:37:10   Log-Likelihood:                 1519.9
No. Observations:                1008   AIC:                            -3034.
Df Residuals:                    1005   BIC:                            -3019.
Df Model:                           2                                         
Covariance Type:            nonrobust                                         
                 coef    std err          t      P>|t|      [0.025      0.975]
------------------------------------------------------------------------------
Intercept      0.0005      0.002      0.270      0.7

In [ ]:
res.cov_type

'nonrobust'

In [ ]:
res.scale

0.0028780590374359455

In [ ]:
np.square(res.resid).sum() / (len(res.resid) - 3)

0.0028780590374359455

In [ ]:
res_huber = utils.sm.RLM(y_in, X_in, M=utils.sm.robust.norms.HuberT()).fit()

In [ ]:
print(res_huber.summary())

                    Robust linear Model Regression Results                    
Dep. Variable:               r_spread   No. Observations:                 1008
Model:                            RLM   Df Residuals:                     1005
Method:                          IRLS   Df Model:                            2
Norm:                          HuberT                                         
Scale Est.:                       mad                                         
Cov Type:                          H1                                         
Date:                Sun, 16 May 2021                                         
Time:                        09:37:10                                         
No. Iterations:                    20                                         
                 coef    std err          z      P>|z|      [0.025      0.975]
------------------------------------------------------------------------------
Intercept   -3.46e-05      0.001     -0.026      0.9

In [ ]:
res_huber.scale

0.03823977409396295

In [ ]:
res_huber.cov_params()

Intercept   r_index      r_equity
Intercept  1.708999e-06 -0.000004  3.936188e-07
r_index   -3.703650e-06  0.000820  4.270397e-04
r_equity   3.936188e-07  0.000427  1.364384e-03

In [ ]:
utils.px.scatter(x=res_huber.sresid, y=res.resid / res.scale, color=X_in.index.get_level_values(0))

### Relative Efficiency of Location Estimates

Here we take the errors from OLS model as a population to work with, calculate various estimates of location across the different model dates and then calculate relative efficienies to see how they compare to the theoretical differences provided in teh Robust Regression lecture notes>

In [ ]:
loc_mean_var = dfs_error["OLS"].groupby("model_date").mean().resid.var()
loc_mean_var

8.662837137890784e-05

In [ ]:
loc_med_var = dfs_error["OLS"].groupby("model_date").median().resid.var()
loc_med_var

0.00017061500052644376

Here the relative efficiency turned out to be 1.96, which is not far from the theoretical $ \frac{\pi}{2} $ from the lecture note.

In [ ]:
loc_med_var / loc_mean_var

1.9695048840313865

Here we calculate the Hodges-Lehman median paired mean estimator. This ended up much higher at 7. vs the 85% in the lecture note. I wonder if this is because there are only four observations in each sample and perhaps this would be different if a larger number of samples were chosen at random.

In [ ]:
mpms = []
for date in dfs_error["OLS"].index.levels[0]:
    mpm = np.median((np.expand_dims(dfs_error["OLS"].loc[date].resid, 0) + np.expand_dims(dfs_error["OLS"].loc[date].resid, 1)) / 2)
    mpms.append(mpm)
loc_mpm_var = np.var(np.array(mpms))
loc_mpm_var

0.0006282412872715555

In [ ]:
fig = utils.go.Figure()
fig.add_scatter(x=dfs_error["OLS"].index.levels[0], y= mpms, name="mpm", mode="markers")
fig.add_scatter(x = dfs_error["OLS"].index.levels[0], y = dfs_error["OLS"].groupby("model_date").mean().resid, name="mean", mode="markers")
fig.add_scatter(x = dfs_error["OLS"].index.levels[0], y = dfs_error["OLS"].groupby("model_date").median().resid, name="median", mode="markers")
fig.update_layout(title_text="Location Estimates - Model Date Samples")
fig.show()

In [ ]:
loc_mpm_var / loc_mean_var

9.561002917852612

Let's try a different sampling methodology to see if we get closer to the theoretical values.


In [ ]:
sample_size = 100
means = []
medians = []
mpms = []
for i in range(100):
    sample = np.random.choice(dfs_error["OLS"].resid, sample_size)
    means.append(np.mean(sample))
    medians.append(np.median(sample))
    mpms.append(np.median((np.expand_dims(sample, 0) + np.expand_dims(sample, 1)) / 2))

### Robust Estimates of Scale

In [ ]:
loc_mean_var = np.var(means)
loc_med_var = np.var(medians)
loc_mpm_var = np.var(mpms)

In [ ]:
loc_med_var / loc_mean_var

0.4184795391195797

In [ ]:
loc_mpm_var / loc_mean_var

0.3738880228901851

In [ ]:
fig = utils.go.Figure()
fig.add_scatter(y= mpms, name="mpm", mode="markers")
fig.add_scatter(y = means, name="mean", mode="markers")
fig.add_scatter(y = medians, name="median", mode="markers")
fig.update_layout(title_text="Location Estimates - Random Samples")
fig.show()